<a href="https://colab.research.google.com/github/NehaChaudhary311/GPT2-Language-Model/blob/master/GAN_Encoder_Decoder.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!pip install transformers

In [0]:

!git clone https://github.com/huggingface/transformers.git

In [0]:
cd transformers

In [0]:
pip install .

In [5]:
cd ..

/content


In [0]:
import torch
import torch.nn as nn
import torch.optim as optim

# from torchtext.datasets import TranslationDataset, Multi30k
from torchtext.data import Field, BucketIterator

import spacy
import numpy as np

import random
import math
import time

In [0]:
SEED = 25

random.seed(SEED)
np.random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)
torch.backends.cudnn.deterministic = True

In [8]:
from GPT2_embedding import gpt2embedding
#for loop on embedding length
zero_embedding = [0 for i in range(768)]
print(len(zero_embedding))

768


In [9]:
import pandas as pd
df = pd.read_csv('HPL.csv')
print(df.head())
print(df.shape)


                                     tokenized_sents
0  It never once occurred to me that the fumbling...
1  Finding nothing else not even gold the Superin...
2  Herbert West needed fresh bodies because his l...
3  The farm like grounds extended back very deepl...
4  His facial aspect too was remarkable for its m...
(5635, 1)


In [0]:
e = gpt2embedding(df['tokenized_sents'][0])

In [30]:
e.tolist()

[[0.039030157029628754,
  -0.08694101125001907,
  0.06618253141641617,
  -0.053096599876880646,
  -0.08796178549528122,
  -0.06879477202892303,
  -0.21709521114826202,
  -0.04100298881530762,
  0.04735622927546501,
  -0.002873989287763834,
  -0.010789135470986366,
  0.0019137200433760881,
  -0.03528137132525444,
  0.06595320254564285,
  0.032943494617938995,
  0.025591742247343063,
  0.06449439376592636,
  0.05800667032599449,
  -0.021951697766780853,
  0.1566760241985321,
  -0.08577790856361389,
  0.033979639410972595,
  -0.10812750458717346,
  -0.009755478240549564,
  0.042683038860559464,
  -0.033145349472761154,
  -0.0016595952911302447,
  0.01673249714076519,
  -0.013796040788292885,
  -0.014151889830827713,
  -0.09284090995788574,
  -0.10636013001203537,
  -0.07592134922742844,
  0.11985501646995544,
  -0.06400191783905029,
  -0.0041628931649029255,
  -0.31933581829071045,
  0.06672101467847824,
  0.058200255036354065,
  0.025514161214232445,
  -0.03067656233906746,
  -0.03246834

In [0]:
#Confining to a limit of words in each sentence
max_words = 200

emb = []
for i in df['tokenized_sents']:
    e = gpt2embedding(i)
    e = e.tolist()
    while(len(e) < max_words):
        e.append(zero_embedding)
    e = e[:200]
    emb.append(e)
df['embeddings'] = emb

In [11]:
print(df['embeddings'])

0       [[0.039030157029628754, -0.08694101125001907, ...
1       [[-0.09350670874118805, 0.0881623923778534, -0...
2       [[0.035637132823467255, -0.09943904727697372, ...
3       [[-0.0686228945851326, -0.020297741517424583, ...
4       [[-0.09653531759977341, -0.04496660456061363, ...
                              ...                        
5630    [[0.02527611516416073, -0.027253521606326103, ...
5631    [[0.012092754244804382, -0.04129645228385925, ...
5632    [[-0.007348539307713509, 0.08950842171907425, ...
5633    [[0.19604724645614624, 0.16463446617126465, 0....
5634    [[0.027969911694526672, -0.08733408898115158, ...
Name: embeddings, Length: 5635, dtype: object


In [32]:
df['embeddings'][0]

[[0.039030157029628754,
  -0.08694101125001907,
  0.06618253141641617,
  -0.053096599876880646,
  -0.08796178549528122,
  -0.06879477202892303,
  -0.21709521114826202,
  -0.04100298881530762,
  0.04735622927546501,
  -0.002873989287763834,
  -0.010789135470986366,
  0.0019137200433760881,
  -0.03528137132525444,
  0.06595320254564285,
  0.032943494617938995,
  0.025591742247343063,
  0.06449439376592636,
  0.05800667032599449,
  -0.021951697766780853,
  0.1566760241985321,
  -0.08577790856361389,
  0.033979639410972595,
  -0.10812750458717346,
  -0.009755478240549564,
  0.042683038860559464,
  -0.033145349472761154,
  -0.0016595952911302447,
  0.01673249714076519,
  -0.013796040788292885,
  -0.014151889830827713,
  -0.09284090995788574,
  -0.10636013001203537,
  -0.07592134922742844,
  0.11985501646995544,
  -0.06400191783905029,
  -0.0041628931649029255,
  -0.31933581829071045,
  0.06672101467847824,
  0.058200255036354065,
  0.025514161214232445,
  -0.03067656233906746,
  -0.03246834

In [33]:
train, validate, test = np.split(df.sample(frac=1), [int(.6*len(df)), int(.8*len(df))])
print(train.shape, validate.shape, test.shape) 

(3381, 2) (1127, 2) (1127, 2)


In [0]:
from itertools import chain
import time
import json
import pickle
import numpy as np
import torch
from torch.autograd import Variable
from torch import nn
from torch import optim
from torch.nn import functional as F
from sklearn.metrics import f1_score, accuracy_score, precision_score, recall_score

In [0]:
class Encoder(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, isCuda):
        super(Encoder, self).__init__()
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        
        self.isCuda = isCuda
        self.lstm = nn.LSTM(input_size, hidden_size, num_layers, batch_first=True)
        self.dropout = nn.Dropout(p=0.2)
        self.leakyrelu = nn.LeakyReLU()
        
        # initializing weights
        nn.init.xavier_uniform_(self.lstm.weight_ih_l0, gain=np.sqrt(2))
        nn.init.xavier_uniform_(self.lstm.weight_hh_l0, gain=np.sqrt(2))
         
    def forward(self, input):
        encoded_input, hidden = self.lstm(input)
        encoded_input = self.leakyrelu(encoded_input)
        return encoded_input

In [0]:
class Decoder(nn.Module):
    def __init__(self, hidden_size, output_size, num_layers, isCuda):
        super(Decoder, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.num_layers = num_layers
        
        self.isCuda = isCuda
        self.lstm = nn.LSTM(hidden_size, output_size, num_layers, batch_first=True)
        self.sigmoid = nn.Sigmoid()
        
        nn.init.xavier_uniform_(self.lstm.weight_ih_l0, gain=np.sqrt(2))
        nn.init.xavier_uniform_(self.lstm.weight_hh_l0, gain=np.sqrt(2))
       
    def forward(self, encoded_input):
        decoded_output, hidden = self.lstm(encoded_input)
        decoded_output = self.sigmoid(decoded_output)
        return decoded_output 

In [0]:
class LSTM_AE(nn.Module):
    def __init__(self, encoder, decoder, isCuda):
        super(LSTM_AE, self).__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.isCuda = isCuda
        
    def forward(self, input):
        encoded_input = self.encoder(input)
        decoded_output = self.decoder(encoded_input)
        return decoded_output

In [0]:
INPUT_SIZE = 768
HIDDEN_SIZE = 512
NUM_LAYERS = 2
OUTPUT_SIZE = 768
IS_CUDA = torch.cuda.is_available()

enc = Encoder(INPUT_SIZE, HIDDEN_SIZE, NUM_LAYERS, IS_CUDA)
dec = Decoder(HIDDEN_SIZE, OUTPUT_SIZE, NUM_LAYERS, IS_CUDA)
model = LSTM_AE(enc, dec, IS_CUDA)

In [19]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

LSTM_AE(
  (encoder): Encoder(
    (lstm): LSTM(768, 512, num_layers=2, batch_first=True)
    (dropout): Dropout(p=0.2, inplace=False)
    (leakyrelu): LeakyReLU(negative_slope=0.01)
  )
  (decoder): Decoder(
    (lstm): LSTM(512, 768, num_layers=2, batch_first=True)
    (sigmoid): Sigmoid()
  )
)

In [0]:
def train_func(train, test, model, epochs):
    
    model.train()
    optimizer = torch.optim.Adam(model.parameters())
    criterion = nn.MSELoss()
    
    print("Started Training ...")
    for epoch in range(epochs):
        start_time = time.time()
        
        train_epoch_loss = 0
        for text in train:
            text = torch.Tensor(text)
            
            text = text.to(device)
            text = text.view(max_words, 1, 768)
            output = model(text)
            loss = criterion(text, output)
            
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
            train_epoch_loss += loss.item()
            
        # test_epoch_loss = 0
        # for text in train_data:
        #     text = torch.Tensor(text)
            
        #     text = text.to(device)
        #     text = text.view(max_words, 1, 768)
        #     output = model(text)
        #     loss = criterion(text, output)
            
        #     optimizer.zero_grad()
        #     loss.backward()
        #     optimizer.step()
            
        #     test_epoch_loss += loss.item()
        
        finish_time = time.time()
        print("Epoch {}: Loss from Training data: {} and Time taken: {}" 
              .format(epoch, train_epoch_loss/len(train), finish_time-start_time))

In [38]:
train_func(train['embeddings'], test['embeddings'], model, 2)

Started Training ...
Epoch 0: Loss from Training data: nan and Time taken: 1362.8792572021484
Epoch 1: Loss from Training data: nan and Time taken: 1366.3346302509308
